In [1]:
import numpy as np
import math

import random
random.seed()

class WeightedUndirectedMatrixGraph:
    
    # initialize a weighted undirected adjacency-matrix graph with n nodes
    #
    def __init__(self, n):
        self._num_vertices = n
        self._adj_matrix = np.zeros((n, n))
        for i in range(n-1):
            for j in range(i+1, n):
                self._adj_matrix[i][j] = math.inf
                self._adj_matrix[j][i] = math.inf
    
    # returns the number of nodes
    #
    def get_num_vertices(self):
        return self._num_vertices
    
    # returns weight of the edge between i and j
    #
    def get_weight(self, i, j):
        return self._adj_matrix[i][j]
    
    # the path is a list of node IDs
    #
    def get_length_of_path(self, path):
        return "METHOD MISSING - NEEDS TO BE IMPLEMENTED"
    
    # print the adjacency matrix
    #
    def output(self):
        print(self._adj_matrix)
    
    # assign weight w to the edge between i and j (both ways)
    # i and j must be different, and both within range(n), and w must be zero or positive
    #
    def set_weight(self, i, j, w):
        if i == j or i < 0 or j < 0 or i >= self._num_vertices or j >= self._num_vertices or w < 0:
            print("Warning: Invalid input to the connect method. Ignoring.")
            return
        self._adj_matrix[i][j] = w
        self._adj_matrix[j][i] = w
    
    # assign random weights to all edges
    #
    def randomize(self):
        for i in range(self._num_vertices - 1):
            for j in range(i+1, self._num_vertices):
                random_weight = 2**random.randrange(self._num_vertices // 2)
                random_weight += random.randrange(2**(self._num_vertices // 2) - 1)
                self.set_weight(i, j, random_weight)
    
    # solve the travelling salesman problem (TSP) by brute force
    #
    # this returns the shortest cycle that visits each node exactly once
    # (also referred to as the shortest Hamilton cycle in the graph:
    #  A Hamilton cycle is a cycle that visits each node exactly once.)
    #
    def solve_TSP_brute_force(self):
        unvisited = {i for i in range(self._num_vertices)}
        unvisited.remove(0)  # select node 0 as the initial and final node of the cycle
        
        # helper method that actually solves the TSP
        #
        shortest_cycle, travel_distance = self._TSP_brute_force(0, 0, unvisited)
        print("Brute-force TSP solver done comparing", \
              WeightedUndirectedMatrixGraph._num_attempts, "cycles.")
        WeightedUndirectedMatrixGraph._num_attempts = 0
        
        return shortest_cycle, travel_distance
    
    # unvisited_nodes is the set of unvisited nodes
    # initial_node is the initial node
    # present_node is the node that is presently visited
    #
    # the method returns the (shortest) remaining path
    # and the length (i.e., total weight) of the shortest remaining path
    #
    # the remaining path is written into the list backward, to exploit faster end-of-list
    # operations on a Python list; since this is a cycle in an undirected graph, it does not matter
    #
    def _TSP_brute_force(self, initial_node, present_node, unvisited_nodes):
        
        # if all nodes are visited, go back to the initial node
        #
        if len(unvisited_nodes) == 0:
            
            WeightedUndirectedMatrixGraph._num_attempts += 1
            if WeightedUndirectedMatrixGraph._num_attempts \
            % WeightedUndirectedMatrixGraph._mod_status_output == 0:
                print("\tChecked", WeightedUndirectedMatrixGraph._num_attempts, "cycles.")
                
            return [initial_node, present_node], self.get_weight(initial_node, present_node)
        
        # check which of the optional next nodes yield the shortest remaining path
        #
        else:
            shortest_remaining_weight = math.inf
            shortest_remaining_path = []
            
            unvisited_nodes_copy = {i for i in unvisited_nodes}
            for v in unvisited_nodes_copy:
                unvisited_nodes.remove(v)
                v_path, v_weight = self._TSP_brute_force(initial_node, v, unvisited_nodes)
                v_path.append(present_node)
                v_weight += self.get_weight(v, present_node)
                unvisited_nodes.add(v)
                
                if v_weight < shortest_remaining_weight:
                    shortest_remaining_weight = v_weight
                    shortest_remaining_path = v_path
            return shortest_remaining_path, shortest_remaining_weight
    
    # static variable used to count number of cycles checked by the brute-force solver
    #
    _num_attempts = 0
    _mod_status_output = 2000000

In [2]:
n = 12

g = WeightedUndirectedMatrixGraph(n)
g.randomize()

g.output()

print("\nPath 0 -> 1 -> 2 has the length", g.get_length_of_path([0, 1, 2]))

[[ 0. 29. 60. 37. 35. 22. 19. 32. 47. 50. 30. 51.]
 [29.  0. 12. 77. 61. 38. 22. 33. 39. 46. 26. 33.]
 [60. 12.  0. 22. 59. 49.  7. 43. 34. 61.  3. 45.]
 [37. 77. 22.  0. 45. 43. 36. 44. 82. 25. 57. 11.]
 [35. 61. 59. 45.  0. 42. 49. 35. 67. 15. 36. 32.]
 [22. 38. 49. 43. 42.  0. 14. 23. 20. 22. 49. 69.]
 [19. 22.  7. 36. 49. 14.  0. 41. 31. 58. 49. 34.]
 [32. 33. 43. 44. 35. 23. 41.  0. 22.  5. 50. 61.]
 [47. 39. 34. 82. 67. 20. 31. 22.  0. 53. 51. 11.]
 [50. 46. 61. 25. 15. 22. 58.  5. 53.  0. 49.  4.]
 [30. 26.  3. 57. 36. 49. 49. 50. 51. 49.  0. 44.]
 [51. 33. 45. 11. 32. 69. 34. 61. 11.  4. 44.  0.]]

Path 0 -> 1 -> 2 has the length METHOD MISSING - NEEDS TO BE IMPLEMENTED


In [3]:
import random

# create a random cycle and determine its distance
#
random_cycle = list(range(n))
random.shuffle(random_cycle)
random_cycle.append(random_cycle[0])

print("Random cycle:", random_cycle)
print("Length of the random cycle:", g.get_length_of_path(random_cycle))

Random cycle: [8, 5, 3, 0, 11, 2, 6, 1, 4, 7, 10, 9, 8]
Length of the random cycle: METHOD MISSING - NEEDS TO BE IMPLEMENTED


In [4]:
# call the TSP solver
#
salesman_path, salesman_travelling_distance = g.solve_TSP_brute_force()

	Checked 2000000 cycles.
	Checked 4000000 cycles.
	Checked 6000000 cycles.
	Checked 8000000 cycles.
	Checked 10000000 cycles.
	Checked 12000000 cycles.
	Checked 14000000 cycles.
	Checked 16000000 cycles.
	Checked 18000000 cycles.
	Checked 20000000 cycles.
	Checked 22000000 cycles.
	Checked 24000000 cycles.
	Checked 26000000 cycles.
	Checked 28000000 cycles.
	Checked 30000000 cycles.
	Checked 32000000 cycles.
	Checked 34000000 cycles.
	Checked 36000000 cycles.
	Checked 38000000 cycles.
Brute-force TSP solver done comparing 39916800 cycles.


In [5]:
print("\nSolution of the TSP:", salesman_path)
print("Minimum travel distance:", salesman_travelling_distance)

print("\nValidate by computing the total length of the cycle:", g.get_length_of_path(salesman_path))


Solution of the TSP: [0, 5, 6, 1, 10, 2, 3, 11, 8, 7, 9, 4, 0]
Minimum travel distance: 208.0

Validate by computing the total length of the cycle: METHOD MISSING - NEEDS TO BE IMPLEMENTED
